## Лабораторна робота №8 
виконала студентка групи ІС-12 мп

Кравчук Олена

Варіант-9

In [0]:
from pyspark.sql.functions import isnan, col
from pyspark.ml.feature import StringIndexer, VectorAssembler, OneHotEncoder, MinMaxScaler
from pyspark.ml.classification import NaiveBayes
from pyspark.sql.types import DoubleType, IntegerType
from pyspark.ml import Pipeline
from pyspark.ml.evaluation import MulticlassClassificationEvaluator, BinaryClassificationEvaluator

In [0]:
schema = '`Id` INT,`is_bad` INT,`emp_length` STRING,`home_ownership` STRING,`annual_inc` STRING,`verification_status` STRING,`pymnt_plan` STRING,`purpose_cat` STRING,`zip_code` STRING,`addr_state` STRING,`debt_to_income` DOUBLE,`delinq_2yrs` STRING,`inq_last_6mths` STRING,`mths_since_last_delinq` STRING,`mths_since_last_record` STRING,`open_acc` STRING,`pub_rec` STRING,`revol_bal` INT,`revol_util` STRING,`total_acc` STRING,`initial_list_status` STRING,`collections_12_mths_ex_med` STRING,`mths_since_last_major_derog` INT,`policy_code` STRING'

In [0]:
df = spark.read.format('csv').option('header', True).option('schema', schema).load("/FileStore/tables/DR_Demo_Lending_Club_reduced.csv")
trainDf, testDf = df.randomSplit([0.8, 0.2])
display(trainDf)

Id is_bad emp_length home_ownership annual_inc verification_status pymnt_plan purpose_cat zip_code addr_state debt_to_income delinq_2yrs inq_last_6mths mths_since_last_delinq mths_since_last_record open_acc pub_rec revol_bal revol_util total_acc initial_list_status collections_12_mths_ex_med mths_since_last_major_derog policy_code 1 0 10 MORTGAGE 50000 not verified n medical 766xx TX 10.87 0 0 NA NA 15 0 12087 12.1 44 f 0 1 PC4 100 0 3 MORTGAGE 200000 VERIFIED - income source n debt consolidation 913xx CA 6.71 0 0 NA NA 11 0 8937 20.8 17 f 0 3 PC5 1000 0 1 MORTGAGE 83000 not verified n home improvement 029xx RI 16.19 0 0 NA NA 12 0 18293 43.1 23 f 0 1 PC1 10000 0 1 RENT 70560 not verified n credit card 900xx CA 16.13 0 1 53 NA 15 0 2304 22.6 34 f 0 2 PC5 1001 1 2 RENT 25000 not verified n debt consolidation 064xx CT 18.05 0 1 NA NA 5 0 9268 47.5 15 f 0 1 PC2 1002 0 10 MORTGAGE 49000 not verified n debt consolidation 847xx UT 6.76 0 0 115 NA 9 0 7121 84.8 22 f 0 3 PC4 1003 0 1 RENT 30000 not verified n debt consolidation 606xx IL 27.04 0 1 76 NA 10 0 6485 13.8 42 f 0 2 PC2 1004 0 1 RENT 40000 not verified n other 991xx WA 0.99 0 1 0 0 1 0 1676 64.5 3 f 0 1 PC4 1005 0 3 MORTGAGE 70000 VERIFIED - income source n other 737xx OK 22.56 0 2 NA NA 11 0 1815 3.5 42 f 0 2 PC1 1006 0 1 RENT 37000 not verified n credit card 752xx TX 17.77 0 0 NA NA 6 0 12242 92.7 8 f 0 1 PC3 1007 0 1 RENT 38500 not verified n debt consolidation 322xx FL 16.71 0 0 NA NA 5 0 8585 93.7 6 f 0 2 PC3 1008 0 3 RENT 52000 VERIFIED - income source n debt consolidation 931xx CA 15.32 0 0 NA NA 8 0 2629 19.7 25 f 0 1 PC4 1010 0 2 RENT 132000 VERIFIED - income n credit card 900xx CA 2.88 0 1 NA NA 5 0 12135 84.9 16 f 0 2 PC5 1011 1 2 RENT 43000 VERIFIED - income n major purchase 851xx AZ 13.51 0 0 48 NA 4 0 275 21.2 5 f 0 2 PC5 1012 0 2 RENT 78504 not verified n debt consolidation 930xx CA 14.03 1 3 12 47 12 1 8473 27.6 29 f 0 2 PC1 1013 0 2 MORTGAGE 50000 not verified n debt consolidation 349xx FL 20.42 1 2 15 0 13 0 12573 71.8 29 f 0 1 PC4 1016 0 1 RENT 34200 not verified n debt consolidation 950xx CA 18.77 0 1 NA NA 8 0 4132 62.6 11 f 0 3 PC3 1017 0 3 RENT 70000 VERIFIED - income source n moving 333xx FL 8.93 0 0 48 NA 7 0 0 0 28 f 0 1 PC1 1019 0 2 RENT 38400 not verified n other 608xx IL 13.59 0 5 NA NA 11 0 7963 50.1 13 f 0 1 PC2 102 0 3 RENT 61000 VERIFIED - income source n vacation 752xx TX 0.98 0 5 NA NA 8 0 1939 6.2 9 f 0 3 PC2 1020 1 2 RENT 26400 VERIFIED - income source n debt consolidation 484xx MI 16.41 0 3 NA NA 13 0 11672 34.5 27 f 0 3 PC3 1021 0 2 RENT 55000 VERIFIED - income n debt consolidation 928xx CA 12.63 0 0 NA NA 12 0 8154 55.8 20 f 0 2 PC4 1022 0 2 RENT 15600 not verified n major purchase 060xx CT 3.62 0 1 NA NA 3 0 1438 59.9 5 f 0 1 PC5 1023 0 5 RENT 42000 not verified n other 902xx CA 10.37 0 0 69 63 3 1 480 96 10 f 0 1 PC1 1024 0 3 RENT 30000 not verified n debt consolidation 073xx NJ 9.8 1 1 19 NA 5 0 5934 39.8 8 f 0 3 PC1 1025 0 3 OWN 48000 not verified n debt consolidation 850xx AZ 5.7 1 0 10 90 8 1 5298 35.1 23 f 0 2 PC3 1028 0 10 MORTGAGE 120000 not verified n major purchase 481xx MI 9.23 1 0 23 NA 16 0 45702 5.3 37 f 0 3 PC5 103 0 7 OWN 61000 VERIFIED - income n house 170xx PA 9.68 0 3 NA 113 7 1 1284 6.3 22 f 0 2 PC4 1031 0 1 RENT 37200 not verified n credit card 336xx FL 8.77 0 0 NA NA 6 0 9945 55.2 8 f 0 3 PC5 1032 1 2 OWN 57600 not verified n home improvement 018xx MA 3.65 1 0 14 NA 10 0 2670 11.7 17 f 0 2 PC1 1033 0 2 MORTGAGE 54900 not verified n home improvement 174xx PA 15.5 0 2 31 86 20 1 2754 40.5 34 f 0 3 PC5 1034 0 2 MORTGAGE 24000 not verified n educational 065xx CT 9.8 0 0 NA NA 7 0 0 0 8 f 0 2 PC3 1037 0 6 MORTGAGE 38400 VERIFIED - income n debt consolidation 620xx IL 13.81 0 3 NA NA 10 0 4922 25.9 18 f 0 3 PC1 1038 1 1 RENT 33600 not verified n major purchase 928xx CA 9.25 0 0 NA NA 9 0 5964 56.3 10 f 0 1 PC5 1039 1 1 RENT 54000 VERIFIED - income source n debt consolidation 114xx NY 6.47 0 0 NA NA 9 0 9041 77.9 11 f 0

In [0]:
display(trainDf.groupby('is_bad').count())

is_bad count 0 6906 1 1047

In [0]:
def getMissingValuesDescription(df):
    return {
        col: df.filter((df[col] == "") | (df[col] == 'NA') | df[col].isNull() | isnan(df[col])).count()
        for col in df.columns
    }

In [0]:
getMissingValuesDescription(df)

Out[266]: {'Id': 0,
 'is_bad': 0,
 'emp_length': 0,
 'home_ownership': 0,
 'annual_inc': 1,
 'verification_status': 0,
 'pymnt_plan': 0,
 'purpose_cat': 0,
 'zip_code': 0,
 'addr_state': 0,
 'debt_to_income': 0,
 'delinq_2yrs': 5,
 'inq_last_6mths': 5,
 'mths_since_last_delinq': 6316,
 'mths_since_last_record': 9160,
 'open_acc': 5,
 'pub_rec': 5,
 'revol_bal': 0,
 'revol_util': 26,
 'total_acc': 5,
 'initial_list_status': 0,
 'collections_12_mths_ex_med': 32,
 'mths_since_last_major_derog': 0,
 'policy_code': 0}

In [0]:
trainDf = trainDf.drop('Id', 'mths_since_last_delinq', 'mths_since_last_record')
testDf = testDf.drop('Id', 'mths_since_last_delinq', 'mths_since_last_record')

In [0]:
def removeRowsWithMissingValues(df):
    for colum in df.columns:
        df = df.filter(~col(colum).isin(['NA']))
    return df

In [0]:
trainDf  = removeRowsWithMissingValues(trainDf)
testDf  = removeRowsWithMissingValues(testDf)

In [0]:
getMissingValuesDescription(trainDf)

Out[270]: {'is_bad': 0,
 'emp_length': 0,
 'home_ownership': 0,
 'annual_inc': 0,
 'verification_status': 0,
 'pymnt_plan': 0,
 'purpose_cat': 0,
 'zip_code': 0,
 'addr_state': 0,
 'debt_to_income': 0,
 'delinq_2yrs': 0,
 'inq_last_6mths': 0,
 'open_acc': 0,
 'pub_rec': 0,
 'revol_bal': 0,
 'revol_util': 0,
 'total_acc': 0,
 'initial_list_status': 0,
 'collections_12_mths_ex_med': 0,
 'mths_since_last_major_derog': 0,
 'policy_code': 0}

In [0]:
display(trainDf)

is_bad emp_length home_ownership annual_inc verification_status pymnt_plan purpose_cat zip_code addr_state debt_to_income delinq_2yrs inq_last_6mths open_acc pub_rec revol_bal revol_util total_acc initial_list_status collections_12_mths_ex_med mths_since_last_major_derog policy_code 0 10 MORTGAGE 50000 not verified n medical 766xx TX 10.87 0 0 15 0 12087 12.1 44 f 0 1 PC4 0 3 MORTGAGE 200000 VERIFIED - income source n debt consolidation 913xx CA 6.71 0 0 11 0 8937 20.8 17 f 0 3 PC5 0 1 MORTGAGE 83000 not verified n home improvement 029xx RI 16.19 0 0 12 0 18293 43.1 23 f 0 1 PC1 0 1 RENT 70560 not verified n credit card 900xx CA 16.13 0 1 15 0 2304 22.6 34 f 0 2 PC5 1 2 RENT 25000 not verified n debt consolidation 064xx CT 18.05 0 1 5 0 9268 47.5 15 f 0 1 PC2 0 10 MORTGAGE 49000 not verified n debt consolidation 847xx UT 6.76 0 0 9 0 7121 84.8 22 f 0 3 PC4 0 1 RENT 30000 not verified n debt consolidation 606xx IL 27.04 0 1 10 0 6485 13.8 42 f 0 2 PC2 0 1 RENT 40000 not verified n other 991xx WA 0.99 0 1 1 0 1676 64.5 3 f 0 1 PC4 0 3 MORTGAGE 70000 VERIFIED - income source n other 737xx OK 22.56 0 2 11 0 1815 3.5 42 f 0 2 PC1 0 1 RENT 37000 not verified n credit card 752xx TX 17.77 0 0 6 0 12242 92.7 8 f 0 1 PC3 0 1 RENT 38500 not verified n debt consolidation 322xx FL 16.71 0 0 5 0 8585 93.7 6 f 0 2 PC3 0 3 RENT 52000 VERIFIED - income source n debt consolidation 931xx CA 15.32 0 0 8 0 2629 19.7 25 f 0 1 PC4 0 2 RENT 132000 VERIFIED - income n credit card 900xx CA 2.88 0 1 5 0 12135 84.9 16 f 0 2 PC5 1 2 RENT 43000 VERIFIED - income n major purchase 851xx AZ 13.51 0 0 4 0 275 21.2 5 f 0 2 PC5 0 2 RENT 78504 not verified n debt consolidation 930xx CA 14.03 1 3 12 1 8473 27.6 29 f 0 2 PC1 0 2 MORTGAGE 50000 not verified n debt consolidation 349xx FL 20.42 1 2 13 0 12573 71.8 29 f 0 1 PC4 0 1 RENT 34200 not verified n debt consolidation 950xx CA 18.77 0 1 8 0 4132 62.6 11 f 0 3 PC3 0 3 RENT 70000 VERIFIED - income source n moving 333xx FL 8.93 0 0 7 0 0 0 28 f 0 1 PC1 0 2 RENT 38400 not verified n other 608xx IL 13.59 0 5 11 0 7963 50.1 13 f 0 1 PC2 0 3 RENT 61000 VERIFIED - income source n vacation 752xx TX 0.98 0 5 8 0 1939 6.2 9 f 0 3 PC2 1 2 RENT 26400 VERIFIED - income source n debt consolidation 484xx MI 16.41 0 3 13 0 11672 34.5 27 f 0 3 PC3 0 2 RENT 55000 VERIFIED - income n debt consolidation 928xx CA 12.63 0 0 12 0 8154 55.8 20 f 0 2 PC4 0 2 RENT 15600 not verified n major purchase 060xx CT 3.62 0 1 3 0 1438 59.9 5 f 0 1 PC5 0 5 RENT 42000 not verified n other 902xx CA 10.37 0 0 3 1 480 96 10 f 0 1 PC1 0 3 RENT 30000 not verified n debt consolidation 073xx NJ 9.8 1 1 5 0 5934 39.8 8 f 0 3 PC1 0 3 OWN 48000 not verified n debt consolidation 850xx AZ 5.7 1 0 8 1 5298 35.1 23 f 0 2 PC3 0 10 MORTGAGE 120000 not verified n major purchase 481xx MI 9.23 1 0 16 0 45702 5.3 37 f 0 3 PC5 0 7 OWN 61000 VERIFIED - income n house 170xx PA 9.68 0 3 7 1 1284 6.3 22 f 0 2 PC4 0 1 RENT 37200 not verified n credit card 336xx FL 8.77 0 0 6 0 9945 55.2 8 f 0 3 PC5 1 2 OWN 57600 not verified n home improvement 018xx MA 3.65 1 0 10 0 2670 11.7 17 f 0 2 PC1 0 2 MORTGAGE 54900 not verified n home improvement 174xx PA 15.5 0 2 20 1 2754 40.5 34 f 0 3 PC5 0 2 MORTGAGE 24000 not verified n educational 065xx CT 9.8 0 0 7 0 0 0 8 f 0 2 PC3 0 6 MORTGAGE 38400 VERIFIED - income n debt consolidation 620xx IL 13.81 0 3 10 0 4922 25.9 18 f 0 3 PC1 1 1 RENT 33600 not verified n major purchase 928xx CA 9.25 0 0 9 0 5964 56.3 10 f 0 1 PC5 1 1 RENT 54000 VERIFIED - income source n debt consolidation 114xx NY 6.47 0 0 9 0 9041 77.9 11 f 0 3 PC2 0 1 RENT 34000 VERIFIED - income source n debt consolidation 926xx CA 19.55 0 0 9 0 23806 76.1 11 f 0 3 PC1 0 4 MORTGAGE 65000 not verified n debt consolidation 295xx SC 13.51 0 4 5 1 4433 33.3 15 f 0 3 PC4 0 1 MORTGAGE 39600 VERIFIED - income source n other 276xx NC 2.64 0 1 4 0 3865 82.2 20 f 0 2 PC5 0 7 MORTGAGE 82000 not verified n debt consolidation 986xx WA 13.19 0 1 8 0 31729 60.3 32 f 0 1 PC1 0 9 MORTGAGE 1270

In [0]:
def convertValues(df):
    df = df.withColumn("is_bad", df["is_bad"].cast(IntegerType()))
    df = df.withColumn("emp_length", df["emp_length"].cast(IntegerType()))
    df = df.withColumn("revol_bal", df["revol_bal"].cast(IntegerType()))
    df = df.withColumn("mths_since_last_major_derog", df["mths_since_last_major_derog"].cast(IntegerType()))
    df = df.withColumn("annual_inc", df["annual_inc"].cast(DoubleType()))
    df = df.withColumn("delinq_2yrs", df["delinq_2yrs"].cast(DoubleType()))
    df = df.withColumn("inq_last_6mths", df["inq_last_6mths"].cast(DoubleType()))
    df = df.withColumn("debt_to_income", df["debt_to_income"].cast(DoubleType()))
    df = df.withColumn("open_acc", df["open_acc"].cast(DoubleType()))
    df = df.withColumn("pub_rec", df["pub_rec"].cast(DoubleType()))
    df = df.withColumn("revol_util", df["revol_util"].cast(DoubleType()))
    df = df.withColumn("total_acc", df["total_acc"].cast(DoubleType()))
    df = df.withColumn("collections_12_mths_ex_med", df["collections_12_mths_ex_med"].cast(DoubleType()))
    return df

In [0]:
trainDf  = convertValues(trainDf)
testDf  = convertValues(testDf)

In [0]:
def getCategoricalColumns(df):
    return [
        item[0] for item in df.dtypes 
        if item[1].startswith('string')
    ]

In [0]:
def getNumericalColumns(df):
    return [
        item[0] for item in df.dtypes 
        if item[1].startswith('int') or item[1].startswith('double')
    ]

In [0]:
categoricalColumns = getCategoricalColumns(trainDf)
categoricalColumns

Out[276]: ['home_ownership',
 'verification_status',
 'pymnt_plan',
 'purpose_cat',
 'zip_code',
 'addr_state',
 'initial_list_status',
 'policy_code']

In [0]:
indexers = [StringIndexer(inputCol=column, outputCol= column+"_index").setHandleInvalid("skip") for column in categoricalColumns]
pipeline = Pipeline(stages=indexers).fit(trainDf)
trainIndexerDf = (pipeline
             .transform(trainDf))
testIndexerDf = (pipeline
             .transform(testDf))

In [0]:
trainIndexerDf = trainIndexerDf.drop(*categoricalColumns)
testIndexerDf = testIndexerDf.drop(*categoricalColumns)

In [0]:
categoricalColumns

Out[279]: ['home_ownership',
 'verification_status',
 'pymnt_plan',
 'purpose_cat',
 'zip_code',
 'addr_state',
 'initial_list_status',
 'policy_code']

In [0]:
encoders = [OneHotEncoder(inputCol=col+"_index", outputCol=col+'_vector') for col in categoricalColumns]
pipeline = Pipeline(stages=encoders).fit(trainIndexerDf)
trainIndexerDf = (pipeline
             .transform(trainIndexerDf))
testIndexerDf = (pipeline
             .transform(testIndexerDf))

In [0]:
display(testIndexerDf)

is_bad emp_length annual_inc debt_to_income delinq_2yrs inq_last_6mths open_acc pub_rec revol_bal revol_util total_acc collections_12_mths_ex_med mths_since_last_major_derog home_ownership_index verification_status_index pymnt_plan_index purpose_cat_index zip_code_index addr_state_index initial_list_status_index policy_code_index home_ownership_vector verification_status_vector pymnt_plan_vector purpose_cat_vector zip_code_vector addr_state_vector initial_list_status_vector policy_code_vector 0 1 40000.0 6.48 0.0 1.0 11.0 0.0 19998 18.3 23.0 0.0 1 0.0 0.0 0.0 6.0 9.0 0.0 0.0 1.0 Map(vectorType -> sparse, length -> 3, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 26, indices -> List(6), values -> List(1.0)) Map(vectorType -> sparse, length -> 698, indices -> List(9), values -> List(1.0)) Map(vectorType -> sparse, length -> 47, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 4, indices -> List(1), values -> List(1.0)) 0 3 36500.0 19.66 1.0 0.0 10.0 0.0 11560 33.7 29.0 0.0 2 1.0 2.0 0.0 3.0 98.0 18.0 0.0 2.0 Map(vectorType -> sparse, length -> 3, indices -> List(1), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(), values -> List()) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 26, indices -> List(3), values -> List(1.0)) Map(vectorType -> sparse, length -> 698, indices -> List(98), values -> List(1.0)) Map(vectorType -> sparse, length -> 47, indices -> List(18), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 4, indices -> List(2), values -> List(1.0)) 0 1 47840.0 24.18 0.0 0.0 8.0 0.0 21507 68.5 8.0 0.0 1 0.0 1.0 0.0 0.0 85.0 2.0 0.0 3.0 Map(vectorType -> sparse, length -> 3, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(1), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 26, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 698, indices -> List(85), values -> List(1.0)) Map(vectorType -> sparse, length -> 47, indices -> List(2), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 4, indices -> List(3), values -> List(1.0)) 0 10 87000.0 14.44 0.0 1.0 5.0 0.0 0 0.0 29.0 0.0 2 1.0 1.0 0.0 0.0 371.0 15.0 0.0 0.0 Map(vectorType -> sparse, length -> 3, indices -> List(1), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(1), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 26, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 698, indices -> List(371), values -> List(1.0)) Map(vectorType -> sparse, length -> 47, indices -> List(15), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 4, indices -> List(0), values -> List(1.0)) 0 10 84000.0 6.67 0.0 0.0 8.0 1.0 12393 63.2 22.0 0.0 3 0.0 0.0 0.0 0.0 36.0 0.0 0.0 1.0 Map(vectorType -> sparse, length -> 3, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 26, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 698, indices -> List(36), values -> List(1.0)) Map(vectorType -> sparse, length -> 47, indices -> List(0), values -> List(1.

In [0]:
categoricalColumns = [col+"_index" for col in categoricalColumns]

In [0]:
trainDf = trainIndexerDf.drop(*categoricalColumns)
testDf = testIndexerDf.drop(*categoricalColumns)

In [0]:
feature_col = trainDf.columns
feature_col.remove('is_bad')
df_assembler = VectorAssembler(inputCols=feature_col, outputCol='features')

In [0]:
trainDf = df_assembler.setHandleInvalid("skip").transform(trainDf)
testDf = df_assembler.setHandleInvalid("skip").transform(testDf)

In [0]:
display(testDf)

is_bad emp_length annual_inc debt_to_income delinq_2yrs inq_last_6mths open_acc pub_rec revol_bal revol_util total_acc collections_12_mths_ex_med mths_since_last_major_derog home_ownership_vector verification_status_vector pymnt_plan_vector purpose_cat_vector zip_code_vector addr_state_vector initial_list_status_vector policy_code_vector features 0 10 49000.0 6.76 0.0 0.0 9.0 0.0 7121 84.8 22.0 0.0 3 Map(vectorType -> sparse, length -> 3, indices -> List(1), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 26, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 697, indices -> List(497), values -> List(1.0)) Map(vectorType -> sparse, length -> 46, indices -> List(28), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 4, indices -> List(), values -> List()) Map(vectorType -> sparse, length -> 792, indices -> List(0, 1, 2, 5, 7, 8, 9, 11, 13, 15, 17, 18, 541, 769, 787), values -> List(10.0, 49000.0, 6.76, 9.0, 7121.0, 84.8, 22.0, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 0 1 40000.0 0.99 0.0 1.0 1.0 0.0 1676 64.5 3.0 0.0 1 Map(vectorType -> sparse, length -> 3, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 26, indices -> List(2), values -> List(1.0)) Map(vectorType -> sparse, length -> 697, indices -> List(), values -> List()) Map(vectorType -> sparse, length -> 46, indices -> List(13), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 4, indices -> List(), values -> List()) Map(vectorType -> sparse, length -> 792, indices -> List(0, 1, 2, 4, 5, 7, 8, 9, 11, 12, 15, 17, 20, 754, 787), values -> List(1.0, 40000.0, 0.99, 1.0, 1.0, 1676.0, 64.5, 3.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 0 1 38500.0 16.71 0.0 0.0 5.0 0.0 8585 93.7 6.0 0.0 2 Map(vectorType -> sparse, length -> 3, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 26, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 697, indices -> List(79), values -> List(1.0)) Map(vectorType -> sparse, length -> 46, indices -> List(2), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 4, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 792, indices -> List(0, 1, 2, 5, 7, 8, 9, 11, 12, 15, 17, 18, 123, 743, 787, 788), values -> List(1.0, 38500.0, 16.71, 5.0, 8585.0, 93.7, 6.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) 0 1 47840.0 24.18 0.0 0.0 8.0 0.0 21507 68.5 8.0 0.0 1 Map(vectorType -> sparse, length -> 3, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 2, indices -> List(1), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 26, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 697, indices -> List(88), values -> List(1.0)) Map(vectorType -> sparse, length -> 46, indices -> List(2), values -> List(1.0)) Map(vectorType -> sparse, length -> 1, indices -> List(0), values -> List(1.0)) Map(vectorType -> sparse, length -> 4, indices -> List(3), values -> List(1.0)) Map(vectorType -> sparse, length -> 792, indices -> List(0, 1, 2, 5, 7, 8, 9, 11, 12, 16, 17, 18, 132, 743, 787, 791), values -> List(1.0, 47840.0, 24.18, 8.0, 21507.0, 68.5, 8.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1

In [0]:
scaler = MinMaxScaler(inputCol='features', outputCol='scaled_features').fit(trainDf)
trainDf = scaler.transform(trainDf)
testDf = scaler.transform(testDf)

In [0]:
nb = NaiveBayes(labelCol='is_bad', \
                featuresCol='scaled_features', \
                modelType='multinomial', \
               smoothing=1)
nbmodel = nb.fit(trainDf)
trainPredictionsDf = nbmodel.transform(trainDf)
testPredictionsDf = nbmodel.transform(testDf)

In [0]:
def getAccuracy(trainPred, testPred):
    evaluator = MulticlassClassificationEvaluator(labelCol='is_bad', predictionCol="prediction", metricName="accuracy") 
    trainNbaccuracy = evaluator.evaluate(trainPred)
    testNbaccuracy = evaluator.evaluate(testPred)
    print("Train accuracy = " + str(trainNbaccuracy))
    print("Test accuracy = " + str(testNbaccuracy))

In [0]:
def getF1(trainPred, testPred):
    evaluator = MulticlassClassificationEvaluator(labelCol='is_bad', predictionCol="prediction", metricName="f1") 
    trainf1 = evaluator.evaluate(trainPred)
    testf1 = evaluator.evaluate(testPred)
    print("Train F1 = " + str(trainf1))
    print("Test F1 = " + str(testf1))

In [0]:
def getROC(trainPred, testPred):
    evaluator = BinaryClassificationEvaluator(rawPredictionCol='probability', labelCol='is_bad')
    print("The area under ROC for train set is {}".format(evaluator.evaluate(trainPred)))
    print("The area under ROC for test set is {}".format(evaluator.evaluate(testPred)))

In [0]:
getAccuracy(trainPredictionsDf, testPredictionsDf)
getF1(trainPredictionsDf, testPredictionsDf)
getROC(trainPredictionsDf, testPredictionsDf)

Train accuracy = 0.8925673064536905
Test accuracy = 0.883150756390193
Train F1 = 0.8580332760558715
Test F1 = 0.8409174771010888
The area under ROC for train set is 0.7558414685986894
The area under ROC for test set is 0.6376403680009354


In [0]:
nb = NaiveBayes(labelCol='is_bad', \
                featuresCol='scaled_features', \
                modelType='gaussian', \
               smoothing=0.9)
nbmodel = nb.fit(trainDf)
trainPredictionsDf = nbmodel.transform(trainDf)
testPredictionsDf = nbmodel.transform(testDf)

In [0]:
getAccuracy(trainPredictionsDf, testPredictionsDf)
getF1(trainPredictionsDf, testPredictionsDf)
getROC(trainPredictionsDf, testPredictionsDf)

Train accuracy = 0.2879041607625918
Test accuracy = 0.2634324465310381
Train F1 = 0.30353049284972133
Test F1 = 0.28420833478640095
The area under ROC for train set is 0.5914264597191426
The area under ROC for test set is 0.5186295637720095


In [0]:
nb = NaiveBayes(labelCol='is_bad', \
                featuresCol='scaled_features', \
                modelType='multinomial', \
               smoothing=0.1)
nbmodel = nb.fit(trainDf)
trainPredictionsDf = nbmodel.transform(trainDf)
testPredictionsDf = nbmodel.transform(testDf)

In [0]:
getAccuracy(trainPredictionsDf, testPredictionsDf)
getF1(trainPredictionsDf, testPredictionsDf)
getROC(trainPredictionsDf, testPredictionsDf)

Train accuracy = 0.8933402035295633
Test accuracy = 0.8768909754825248
Train F1 = 0.8628518548191706
Test F1 = 0.8381108520612208
The area under ROC for train set is 0.7868027259248654
The area under ROC for test set is 0.6236881269448598
